In [3]:
import pandas as pd
import numpy as np
import sys, glob, pickle
from pathlib import Path
import mlflow
import plotly.express as px
import plotly.graph_objects as go

# Repo root (adjust if notebook moved)
project_root = Path.cwd().parent
if str(project_root) not in sys.path:
    sys.path.append(str(project_root))

from src.utils.paths import PROCESSED_DIR, PRODUCTION_DIR

In [4]:
# Locate latest feature parquet (pattern sensor_496_features_*.parquet)
feature_files = sorted(glob.glob(str(PROCESSED_DIR / 'sensor_496_features_*.parquet')))
if not feature_files:
    raise FileNotFoundError('No feature parquet found (pattern sensor_496_features_*.parquet)')
FEATURE_PATH = feature_files[-1]
print('Using feature file:', FEATURE_PATH)
df = pd.read_parquet(FEATURE_PATH)
df.head()

Using feature file: /home/ivanseldasp/ds_projects/5_bcn_noise_AB_testing_git/data/processed/sensor_496_features_a746138651a2.parquet


Id_Instal  Noise_db  hour  day_of_week  month  year  \
2015-12-07 00:00:00      496.0      69.0     0            0     12  2015   
2015-12-07 01:00:00      496.0      66.6     1            0     12  2015   
2015-12-07 02:00:00      496.0      65.5     2            0     12  2015   
2015-12-07 03:00:00      496.0      63.9     3            0     12  2015   
2015-12-07 04:00:00      496.0      62.6     4            0     12  2015   

                       Latitud  Longitud  
2015-12-07 00:00:00  41.374878  2.161585  
2015-12-07 01:00:00  41.374878  2.161585  
2015-12-07 02:00:00  41.374878  2.161585  
2015-12-07 03:00:00  41.374878  2.161585  
2015-12-07 04:00:00  41.374878  2.161585

In [5]:
# Basic inspection
print('Rows:', len(df))
print('Columns:', len(df.columns))
print('Columns sample:', df.columns[:15].tolist())

# Try to identify target column
target_col = 'Noise_db' if 'Noise_db' in df.columns else None
if target_col is None:
    # heuristic: look for something like 'noise' (case-insensitive)
    for c in df.columns:
        if 'noise' in c.lower() and 'lag' not in c.lower():
            target_col = c; break
if target_col is None:
    raise ValueError('Target column not found. Expected Noise_db.')
print('Target column:', target_col)

Rows: 70728
Columns: 8
Columns sample: ['Id_Instal', 'Noise_db', 'hour', 'day_of_week', 'month', 'year', 'Latitud', 'Longitud']
Target column: Noise_db


In [6]:
# Prepare features (drop obviously non-feature columns)
drop_cols = {target_col, 'Id_Instal', 'feature_hash', 'hash', 'datetime'} & set(df.columns)
feature_cols = [c for c in df.columns if c not in drop_cols]
X = df[feature_cols].astype(float).values
y = df[target_col].astype(float).values
print('Feature cols:', len(feature_cols))

Feature cols: 6


In [7]:
# Load production model (pickle)
model_path = PRODUCTION_DIR / 'model.pkl'
if not model_path.exists():
    raise FileNotFoundError(f'Model not found at {model_path}')
with open(model_path, 'rb') as f:
    model = pickle.load(f)
print('Model loaded:', type(model))

Model loaded: <class 'xgboost.sklearn.XGBRegressor'>


In [8]:
# Expanding one-step backtest (in-memory)
initial_window = 500
seasonal_lag = 24
stride = 1
indices = list(range(initial_window, len(y), stride))

y_true_list = []
y_pred_list = []
naive_last_list = []
naive_seas_list = []

for t in indices:
    # Predict point t using model already trained on full dataset (production scenario)
    # If you want true walk-forward retraining, re-fit with X[:t], y[:t] here (slower).
    y_hat = model.predict(X[t:t+1])[0]
    y_pred_list.append(y_hat)
    y_true_list.append(y[t])
    nl = y[t-1]
    ns = y[t-seasonal_lag] if t - seasonal_lag >= 0 else nl
    naive_last_list.append(nl)
    naive_seas_list.append(ns)

bt_df = pd.DataFrame({
    'idx': indices,
    'actual': y_true_list,
    'model': y_pred_list,
    'naive_last': naive_last_list,
    'naive_seasonal': naive_seas_list
})
bt_df.head()

idx  actual      model  naive_last  naive_seasonal
0  500    71.7  72.148628        71.3            71.2
1  501    70.9  71.887978        71.7            80.0
2  502    69.5  70.605469        70.9            70.2
3  503    70.4  70.570572        69.5            70.2
4  504    67.5  68.444016        70.4            69.4

In [9]:
# Metrics
def rmse(a,b): return float(np.sqrt(np.mean((np.asarray(a)-np.asarray(b))**2)))
def mae(a,b): return float(np.mean(np.abs(np.asarray(a)-np.asarray(b))))
def smape(a,b):
    a,b = np.asarray(a), np.asarray(b)
    return float(100*np.mean(np.abs(a-b)/( (np.abs(a)+np.abs(b))/2 + 1e-9)))

model_rmse = rmse(bt_df.actual, bt_df.model)
model_mae = mae(bt_df.actual, bt_df.model)
naive_rmse = rmse(bt_df.actual, bt_df.naive_last)
seasonal_rmse = rmse(bt_df.actual, bt_df.naive_seasonal)
improv_last = (naive_rmse - model_rmse)/naive_rmse*100 if naive_rmse else 0
improv_seas = (seasonal_rmse - model_rmse)/seasonal_rmse*100 if seasonal_rmse else 0

resid = bt_df.actual - bt_df.model
summary_metrics = {
    'model_rmse': model_rmse,
    'model_mae': model_mae,
    'smape': smape(bt_df.actual, bt_df.model),
    'naive_last_rmse': naive_rmse,
    'naive_seasonal_rmse': seasonal_rmse,
    'improvement_vs_last_%': improv_last,
    'improvement_vs_seasonal_%': improv_seas,
    'points': len(bt_df)
}
pd.Series(summary_metrics)

model_rmse                       1.543351
model_mae                        1.022166
smape                            1.490882
naive_last_rmse                  2.116141
naive_seasonal_rmse              2.206435
improvement_vs_last_%           27.067663
improvement_vs_seasonal_%       30.052279
points                       70228.000000
dtype: float64

In [10]:
# Plot: Actual vs predictions
fig_main = px.line(bt_df, x='idx', y=['actual','model','naive_last','naive_seasonal'],
                   labels={'value':'dB','variable':'Series'},
                   title='Actual vs Model & Baselines')
fig_main.update_traces(line=dict(width=1.3))
fig_main.show()

In [11]:
# Residual distribution
bt_df['residual'] = resid
bt_df['abs_err'] = bt_df.residual.abs()
fig_resid = px.histogram(bt_df, x='residual', nbins=50, title='Residual Distribution (Model)')
fig_resid.add_vline(x=0, line_dash='dash', line_color='black')
fig_resid.show()

fig_abs = px.histogram(bt_df, x='abs_err', nbins=50, title='Absolute Error Distribution (Model)')
fig_abs.show()
print('Residual mean:', resid.mean(), '| std:', resid.std())

Residual mean: 0.0005343147519380916 | std: 1.5433622268478076


In [12]:
# Rolling RMSE
WINDOW = 100
bt_df['sq_err'] = bt_df.residual**2
bt_df['rolling_rmse'] = (bt_df.sq_err.rolling(WINDOW).mean())**0.5
fig_roll = px.line(bt_df, x='idx', y='rolling_rmse', title=f'Rolling RMSE (window={WINDOW})')
fig_roll.add_hline(y=model_rmse, line_dash='dash', line_color='orange', annotation_text='Global RMSE')
fig_roll.show()

In [ ]:
# Empirical 95% prediction interval
alpha=0.05
q_low = resid.quantile(alpha/2)
q_high = resid.quantile(1-alpha/2)
bt_df['lower_emp'] = bt_df.model + q_low
bt_df['upper_emp'] = bt_df.model + q_high
coverage = ((bt_df.actual>=bt_df.lower_emp) & (bt_df.actual<=bt_df.upper_emp)).mean()*100
avg_width = (bt_df.upper_emp - bt_df.lower_emp).mean()
print(f'Empirical 95% coverage: {coverage:.2f}% | Avg width: {avg_width:.2f} dB')

WEEK_HOURS = 24*10
week_df = bt_df.tail(WEEK_HOURS).copy()  # adjust if your data is not hourly"
print(f'Zoom window points: {len(week_df)} (idx range {week_df.idx.min()} - {week_df.idx.max()})')
      
fig_ci_week = go.Figure()
fig_ci_week.add_trace(go.Scatter(x=week_df.idx, y=week_df.model, name='Prediction', mode='lines', line=dict(color='blue')))
fig_ci_week.add_trace(go.Scatter(x=week_df.idx, y=week_df.upper_emp, name='Upper', mode='lines', line=dict(width=0)))
fig_ci_week.add_trace(go.Scatter(x=week_df.idx, y=week_df.lower_emp, name='Lower', mode='lines', fill='tonexty', fillcolor='rgba(0,123,255,0.18)', line=dict(width=0)))
fig_ci_week.add_trace(go.Scatter(x=week_df.idx, y=week_df.actual, name='Actual', mode='lines', line=dict(color='black', width=1)))
fig_ci_week.update_layout(title='Empirical 95% Interval – Last 10 Days', xaxis_title='idx', yaxis_title='dB')
fig_ci_week.show()

Empirical 95% coverage: 95.00% | Avg width: 6.18 dB
Zoom window points: 240 (idx range 70488 - 70727)


In [14]:
# Error by pseudo-hour (idx mod 24)
bt_df['hour_proxy'] = bt_df.idx % 24
fig_hour = px.box(bt_df, x='hour_proxy', y='abs_err', title='Absolute Error by Hour (proxy)')
fig_hour.show()